### Script pour le controle des données brutes issues de la chaine INSIGHT
### Etude de conformité des fichiers

In [1]:
%%writefile ".env"

PROJECT_ID="feux_cq"

COMMUN_PATH = "N:/"
PATH_INFOCENTRE_APP = ${COMMUN_PATH}Informatique/SIG/Application/Jupyterhub/
PATH_ETUDE = ${COMMUN_PATH}Informatique/SIG/Donnees/Oeil/Traitement_Donnees/SURFACES_BRULEES_SENTINEL/2022/220502_PreparationFeu2020/
PROJECT_PATH =${COMMUN_PATH}Informatique/SIG/Application/Jupyterhub/projets/catalogFiles/
DATA_CATALOG_DIR = ${PATH_INFOCENTRE_APP}projets/catalogFiles/ 
DATA_OUTPUT_DIR = ${PROJECT_PATH}output/
SIG_DATA_PATH = ${COMMUN_PATH}Informatique/SIG/Donnees/
DB_USER="jfnguyenvansoc"
DB_PWD="oeil"
DB_HOST="172.20.12.13"
DB_PORT=5432

DB_WORKSPACE="oeil_traitement"
DB_REF="oeil_reference"
DB_EXT="data_externe"
DB_SCHEMA = "feux_cq"
DB_SCHEMA_REF = "feux"

Overwriting .env


In [2]:
import logging
from filecmp import dircmp
from os import listdir
import os
import filecmp
from dotenv import load_dotenv
from intake import open_catalog
import matplotlib as plt
import pandas as pd
import numpy as np
from shapely import wkt
import shapely
from sqlalchemy import create_engine
from shapely.geometry import shape
from shapely.ops import unary_union
from geopandas import GeoDataFrame
import geopandas as gpd
from datetime import datetime
import networkx as nx
from shapely.geometry import MultiPolygon
from dotenv import find_dotenv

env_file = find_dotenv("N:\Informatique\SIG\Etudes\2023\2309_QC_feux\Travail\Scripts\CQ_sentinel_surfaces_brulees\Controle\.env")
load_dotenv()

## Create log file 
logging.basicConfig(filename='N:/Informatique/SIG/Etudes/2023/2309_QC_feux/Travail/Scripts/CQ_sentinel_surfaces_brulees/Controle/{:%Y-%m-%d}_Controle_data_brute.log'.format(datetime.now()),filemode='w', encoding='utf-8', level=logging.INFO, force=True, format='%(message)s')

##open yaml file to get raw buned area table
catfeux = open_catalog(f'{os.getenv("PROJECT_PATH")}/Fire_Detection_Data_Quality.yaml')

surfdetect_control = catfeux.Surfaces_brulees_brute_control.read()

date_start=pd.to_datetime("2017-01-01", format="%Y-%m-%d")
date_end=pd.to_datetime("2017-12-31", format="%Y-%m-%d")

## Début des contrôles

In [3]:
def get_all_elements_in_list_of_lists(list):
    count = 0
    for element in list:
        count += len(element)
    return count

In [5]:
surfdetect_control

nom       province      commune    surface  \
0      SENTINEL2x_20170924_L2A_T58KDC  Province Nord  KAALA GOMEN   4.233149   
1      SENTINEL2x_20170924_L2A_T58KDC  Province Nord  KAALA GOMEN   2.852124   
2      SENTINEL2x_20170924_L2A_T58KDC  Province Nord    HIENGHENE   2.812227   
3      SENTINEL2x_20170924_L2A_T58KDC  Province Nord  KAALA GOMEN   4.753280   
4      SENTINEL2x_20170924_L2A_T58KDC  Province Nord  KAALA GOMEN   1.210839   
...                               ...            ...          ...        ...   
33004  SENTINEL2x_20170924_L2A_T58KDC  Province Nord    HIENGHENE   2.111671   
33005  SENTINEL2x_20170924_L2A_T58KDC  Province Nord    HIENGHENE   1.311038   
33006  SENTINEL2x_20170924_L2A_T58KDC  Province Nord    HIENGHENE   1.341059   
33007  SENTINEL2x_20170924_L2A_T58KDC  Province Nord    HIENGHENE   1.090859   
33008  SENTINEL2x_20170924_L2A_T58KDC  Province Nord  KAALA GOMEN  13.569382   

                                                geometry       date_  \
0      MULTIPOLYGON (((164.564 -20.677, 164.566 -20.6...  2017-09-24   
1      MULTIPOLYGON (((164.572 -20.677, 164.572 -20.6...  2017-09-24   
2      MULTIPOLYGON (((164.913 -20.677, 164.913 -20.6...  2017-09-24   
3      MULTIPOLYGON (((164.375 -20.675, 164.375 -20.6...  2017-09-24   
4      MULTIPOLYGON (((164.385 -20.678, 164.386 -20.6...  2017-09-24   
...                                                  ...         ...   
33004  MULTIPOLYGON (((164.876 -20.675, 164.876 -20.6...  2017-09-24   
33005  MULTIPOLYGON (((164.888 -20.676, 164.888 -20.6...  2017-09-24   
33006  MULTIPOLYGON (((164.867 -20.676, 164.867 -20.6...  2017-09-24   
33007  MULTIPOLYGON (((164.855 -20.679, 164.855 -20.6...  2017-09-24   
33008  MULTIPOLYGON (((164.369 -20.668, 164.369 -20.6...  2017-09-24   

                             surface_id_h3   nom_court  
0      L2A_T58KDC_20170924_8c9f5e691da53ff  L2A_T58KDC  
1      L2A_T58KDC_20170924_8c9f5e690a2e9ff  L2A_T58KDC  
2      L2A_T58KDC_20170924_8c9e2db26a4a7ff  L2A_T58KDC  
3      L2A_T58KDC_20170924_8c9f5ad2d6b51ff  L2A_T58KDC  
4      L2A_T58KDC_20170924_8c9f5ad2d584dff  L2A_T58KDC  
...                                    ...         ...  
33004  L2A_T58KDC_20170924_8c9e2db214ea5ff  L2A_T58KDC  
33005  L2A_T58KDC_20170924_8c9e2db2021c3ff  L2A_T58KDC  
33006  L2A_T58KDC_20170924_8c9e2db2e9a61ff  L2A_T58KDC  
33007  L2A_T58KDC_20170924_8c9e2db2eb28bff  L2A_T58KDC  
33008  L2A_T58KDC_20170924_8c9f5ad29d85bff  L2A_T58KDC  

[33009 rows x 8 columns]

### Check if tile's name are differents than the 15 use in NC

In [4]:
logging.info('------------------------------------------------')
logging.info('Check if unknown tiles are found in data')
logging.info('------------------------------------------------')

## liste des 15 tuiles présentes sur la GT et les iles 
list_tiles=['L2A_T58KCC','L2A_T58KCD','L2A_T58KDB','L2A_T58KDC','L2A_T58KEA','L2A_T58KEB','L2A_T58KEC',
            'L2A_T58KFA','L2A_T58KFB','L2A_T58KFC','L2A_T58KGA','L2A_T58KGB','L2A_T58KGC','L2A_T58KGV','L2A_T58KHB']

## prendre que le numéro de la dalle pour les traitements
surfdetect_control['nom_court'] = [x[-10:] for x in surfdetect_control['nom']]

error_tile=[]

for i in range(len(surfdetect_control)):
    if surfdetect_control['nom_court'][i] in list_tiles:
         continue
    else:
        error_tile.append(surfdetect_control.iloc[i]) ## on regarde si d'autres tuiles sont présentes dans le jeu de donnée

if not error_tile:
    print('Aucune tuiles détectées en dehors des 15 tuiles utilisées par l algorithme')
    logging.info('Not unkonw tiles found in data - continue process')
    len_error_tile=0
else:
    error_tile=pd.concat(error_tile,axis=1, ignore_index=True).T
    print('Attention des tuiles en dehors des tuiles abituelles sont présentes dans le jeux de donnée')
    logging.error('%s !! WARNING !! Unknow tile found in data - check surface_id_h3 number above or in code !! :', error_tile['surface_id_h3']) ## on alimente le log si présence de tuiles autres
    len_error_tile=len(error_tile)

logging.info('Number of tiles detected outside the 15 tiles', len_error_tile)

Aucune tuiles détectées en dehors des 15 tuiles utilisées par l algorithme


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

### Check if tile occurence is equal to zero

In [12]:
### Check if tile occurence is equal to zero
## traitement à prendre avec des pincettes car selon la résolution temporelle des données des tuiles peuvent manquer 

logging.info('------------------------------------------------')
logging.info('Check if tile occurence')
logging.info('------------------------------------------------')

df_dalle=pd.DataFrame({"date_":surfdetect_control.date_,"dalle_names":surfdetect_control.nom_court})
## prendre que le numéro de la dalle
df_dalle['dalle_names'] = [x[-10:] for x in df_dalle['dalle_names']]
df_dalle=df_dalle.set_index(df_dalle['date_'])
df_dalle = df_dalle.sort_index()

occurrences_dalles = df_dalle["dalle_names"].value_counts()
print(occurrences_dalles)

logging.info('%s !! Tile occurence - check tile name above or in code !! :', occurrences_dalles)

dalle_names
L2A_T58KDC    10250
L2A_T58KDB     7989
L2A_T58KEB     6817
L2A_T58KFA     3319
L2A_T58KEA     1753
L2A_T58KFB     1250
L2A_T58KCC      590
L2A_T58KEC      539
L2A_T58KGB      113
L2A_T58KCD      107
L2A_T58KGA       80
L2A_T58KHB       77
L2A_T58KFC       62
L2A_T58KGC       46
L2A_T58KGV       17
Name: count, dtype: int64


### Check if burned area are under 1ha

In [14]:
## Check if burned area are under 1ha

logging.info('------------------------------------------------')
logging.info('Check if burned areas are not under 1 ha')
logging.info('------------------------------------------------')

error_surface=[]

for i in range(len(surfdetect_control)):
    if surfdetect_control['surface'][i] >= 1:
         continue
    else:
        error_surface.append(surfdetect_control.iloc[i])

if not error_surface:
    print('empty_list')
    logging.info('No surface found under 1ha - continue process')
    len_error_surface=0
else:
    error_surface=pd.concat(error_surface,axis=1, ignore_index=True).T
    print('list if not empty')
    logging.info('%s !! WARNING !! burned areas are found under 1 ha - check ogc_fid number above or in code !! :', error_surface['surface_id_h3'])
    len_error_surface=len(error_surface)

logging.info('Number polygons under 1ha ', len_error_surface)

empty_list


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

### Check if geometries have errors

In [16]:
## Check if burned area have wrong geometries

logging.info('------------------------------------------------')
logging.info('Check if burned areas have wrong geometries')
logging.info('------------------------------------------------')

is_valid = surfdetect_control.geometry.is_valid
invalid_geometries = surfdetect_control[~is_valid]
len_invalid_geometries=len(invalid_geometries)

print("Multipolygones with geometries errors :",invalid_geometries)
logging.error('%s !! WARNING !! burned areas geometries have errors - check surface_id_h3 above or in code !! :', invalid_geometries.surface_id_h3)

surfdetect_control.geometry = surfdetect_control.geometry.buffer(0) # correct the geometry

## check if the correction is applied
is_valid_after_correction = surfdetect_control.geometry.is_valid
invalid_geometries_after_correction = surfdetect_control[~is_valid_after_correction]
print("Check if geometry correction were applied :", invalid_geometries_after_correction)
logging.error('%s !! WARNING !! a geometry correction were applied - if empty continue process : ',invalid_geometries_after_correction)

Multipolygones with geometries errors : Empty GeoDataFrame
Columns: [nom, province, commune, surface, geometry, date_, surface_id_h3, nom_court]
Index: []
Check if geometry correction were applied : Empty GeoDataFrame
Columns: [nom, province, commune, surface, geometry, date_, surface_id_h3, nom_court]
Index: []


#### Check if burned areas are detected outside date interval set at the begening

In [17]:
## Check if burned areas are detected outside date interval set at the begening

logging.info('------------------------------------------------')
logging.info('%s Check if burned areas are included into the following date interval', )
logging.info('------------------------------------------------')

error_date=[]

for i in range(len(surfdetect_control)):
    current_date = pd.to_datetime(surfdetect_control['date_'][i])
    
    if date_start <= current_date <= date_end:
        continue
    else:
        error_date.append(surfdetect_control.iloc[i])

if not error_date:
    print('empty_list')
    logging.info('Burned areas are included into date range - continue process')
    len_outside_date=0
else:
    error_date=pd.concat(error_date,axis=1, ignore_index=True).T
    print('list if not empty')
    logging.error('%s !! WARNING !! burned areas are found outside date range - check surface_id_h3 above or in code !! :', error_date['surface_id_h3'])
    len_outside_date=len(error_date)

logging.info('Number polygons outiside the date range ', len_outside_date)

empty_list


--- Logging error ---
Traceback (most recent call last):
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 1110, in emit
    msg = self.format(record)
          ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "c:\Users\oriane.bruyere\AppData\Local

In [18]:
## create an id
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

### Check if identical geometries are observed at a same date

In [19]:
#check if identical geometries are observed at a same date
len_surfdetect_control_before=len(surfdetect_control)
def compare_geometries(gdf):
    geometry_date_dict = {}

    for index, row in gdf.iterrows():
        geometry =  row['geometry']
        date = row['date_']

        # Convertir la géométrie en une forme Shapely
        geom_shape = shape(geometry)
        key = (geom_shape, date)

        # Ajouter la paire (forme, date) au dictionnaire
        if key not in geometry_date_dict:
            geometry_date_dict[key] = []

        geometry_date_dict[key].append(index)
    identique_geom=[]
    
    # identifier les géométries avec la même forme à la même date = doublon
    for key, indices in geometry_date_dict.items():
        if len(indices) > 1:
            identique_geom.append(indices)
            print(f"Géométries identiques à la même date : {indices}")
    
    return(identique_geom)

surfdetect_control['geometry']=shapely.wkt.loads(shapely.wkt.dumps(surfdetect_control['geometry'], rounding_precision=5)) ## change number of decimal for geometry
identique_geom=compare_geometries(surfdetect_control) 

logging.info('------------------------------------------------')
logging.info('%s Check if 2 identical geometries shape are observed at a same date', )
logging.info('------------------------------------------------')

if not identique_geom:
    print('empty_list')
    logging.info('NO identical geometries found at the same date - continue process')
    len_identique_geom=0
else:
    print('list if not empty')
    len_identique_geom=len(identique_geom)
    #logging.error('%s !! WARNING !! same geometries at a same date were found - check ogc_fid number above or in code !! :', identique_geom.index)
    
    ### if identical geometries are found : check if they have the name tile name
    for sublist in identique_geom:
        nom_values = [surfdetect_control.loc[i, 'nom_court'] for i in sublist]
        index_values=[surfdetect_control.loc[i, 'ID'] for i in sublist]
        if all(value == nom_values[0] for value in nom_values):
            print('nom de thuile identique')
            logging.error('%s !! WARNING !! same geometries at a same date were found on a same tile: check above for informations',index_values)
            
            ## we keep the first geom et delete the others
            if len(sublist) == 2: 
                surfdetect_control=surfdetect_control.drop(sublist[1])
                print('delete index : ',sublist[1])
                logging.error('%s !! DELETE !! geometry deleted : check above for informations',sublist[1])
            else:
                surfdetect_control=surfdetect_control.drop(sublist[1:])
                print('delete index :',sublist[1:])
                logging.error('%s !! DELETE !! geometry deleted : check above for informations',sublist[1:])
        else:
            print('nom de thuile différente')
            logging.error('%s !! WARNING !! same geometries at a same date were found on different tiles : check above for informations',index_values)
            
            ## we keep the first geom et delete the others
            if len(sublist) == 2: 
                surfdetect_control=surfdetect_control.drop(sublist[1])
                print('delete index : ',sublist[1])
                logging.error('%s !! DELETE !! geometry deleted : check above for informations',sublist[1])
            else:
                surfdetect_control=surfdetect_control.drop(sublist[1:])
                print('delete index :',sublist[1:])
                logging.error('%s !! DELETE !! geometry deleted : check above for informations',sublist[1:])

surfdetect_control=surfdetect_control.reset_index(drop=True)
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

Géométries identiques à la même date : [135, 32494]
Géométries identiques à la même date : [151, 32512]
Géométries identiques à la même date : [959, 966]
Géométries identiques à la même date : [3019, 29081]
Géométries identiques à la même date : [3092, 3784]
Géométries identiques à la même date : [4007, 4183]
Géométries identiques à la même date : [6641, 7022]
Géométries identiques à la même date : [6654, 7033]
Géométries identiques à la même date : [8023, 8466]
Géométries identiques à la même date : [8826, 9602]
Géométries identiques à la même date : [10455, 11190]
Géométries identiques à la même date : [10465, 11208]
Géométries identiques à la même date : [10496, 11237]
Géométries identiques à la même date : [12682, 13372]
Géométries identiques à la même date : [12746, 13309]
Géométries identiques à la même date : [12761, 13329]
Géométries identiques à la même date : [12786, 13348]
Géométries identiques à la même date : [12818, 13366]
Géométries identiques à la même date : [16453, 16

## Overlapping polygons for a same date

### Create intersected group of polygons at a same date

In [21]:
def find_intersecting_id(row, gdf):
    # Filtrer le GeoDataFrame pour les polygones à la même date
    gdf_same_date = gdf[gdf['date_'] == row['date_']]
    
    # Utiliser `sindex` pour une recherche spatiale plus efficace parmi ceux de la même date
    possible_matches_index = list(gdf_same_date.sindex.intersection(row['geometry'].bounds))
    possible_matches = gdf_same_date.iloc[possible_matches_index]
    precise_matches = possible_matches[possible_matches.geometry.intersects(row['geometry'])]
    
    intersecting_ids = precise_matches['ID'].tolist()
    intersecting_ids = [id_ for id_ in intersecting_ids if id_ != row['ID']]
    
    return intersecting_ids

G = nx.Graph()
for index, row in surfdetect_control.iterrows():
    intersecting_ids = find_intersecting_id(row, surfdetect_control)
    for id_ in intersecting_ids:
        G.add_edge(row['ID'], id_)

groupes = list(nx.connected_components(G))
for groupe_id, groupe in enumerate(groupes):
    for id_ in groupe:
        surfdetect_control.loc[surfdetect_control['ID'] == id_, 'groupe_id'] = groupe_id

### Check if overlapping geometries are around tile's limit

In [26]:
tile_stl2 = catfeux.tile_sentinel2_line_UTM.read() ## ouvirr la table des limites des tuiles Sentinel2
tile_stl2=tile_stl2.set_index(tile_stl2['Name']) ## mettre en index le nom de la tuile

group_ids = surfdetect_control['groupe_id'].unique()
delete_index_tiles_limits=[]

logging.info('------------------------------------------------')
logging.info('%s Check if overlapping geometries at a same date are observed close to tile limits ', )
logging.info('------------------------------------------------')

for group_id in group_ids:
    # Sélectionnez les données pour le groupe en cours
    group_data = surfdetect_control[surfdetect_control['groupe_id'] == group_id]
    group_data['nom_court']= [x[-5:] for x in group_data['nom_court']]
    if group_data.shape[0] >= 2 :

        for i in range(len(group_data)):
            if group_data.iloc[i]['geometry'].buffer(20).intersects(tile_stl2['geometry'].loc[group_data.iloc[i]['nom_court']]):
                print("tile touche",group_data.iloc[i]["ID"]-1)
                surfdetect_control.drop(group_data.iloc[i]["ID"]-1,inplace=True)
                logging.error('%s !! WARNING !! Intersection between geometry and tile limits were found : check above for informations',group_data.iloc[i]["ID"]-1)
                delete_index_tiles_limits.append(group_data.iloc[i]["ID"]-1)

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

### Check if overlapping geometries are from differents tiles

In [27]:
group_ids = surfdetect_control['groupe_id'].unique()
delete_index_same_tiles_geom=[]

logging.info('------------------------------------------------')
logging.info('%s Check if overlapping geometries at a same date are observed from a same tile ', )
logging.info('------------------------------------------------')

for group_id in group_ids:
    
    group_data = surfdetect_control[surfdetect_control['groupe_id'] == group_id]
    group_data['nom_court']= [x[-5:] for x in group_data['nom_court']]
    if group_data.shape[0] >= 2 :
        if all(v == group_data['nom_court'].iloc[0] for v in group_data['nom_court']):
            print(f"les noms des tuiles sont identiques.", group_data)
            logging.error('%s !! WARNING !! overlapping geometries at a same date were found on a same tile : check above for informations',group_data)
        
        else: ## we merge geometries overlapping from differents tiles
            print(f"les noms des tuiles sont différents")
            nouveau_polygone = unary_union(group_data['geometry'])
            surfdetect_control.at[group_data.iloc[0]["ID"]-1,'geometry'] = nouveau_polygone
            surfdetect_control.drop(group_data.iloc[1:]["ID"]-1,inplace=True)
            delete_index_same_tiles_geom.append(group_data.iloc[i]["ID"]-1)


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont identiques.                                nom       province    commune   surface  \
18  SENTINEL2x_20170924_L2A_T58KDC  Province Nord  HIENGHENE  1.030788   
26  SENTINEL2x_20170924_L2A_T58KDC  Province Nord  HIENGHENE  9.687402   

                                             geometry       date_  \
18  POLYGON ((164.684 -20.683, 164.685 -20.683, 16...  2017-09-24   
26  POLYGON ((164.686 -20.682, 164.686 -20.682, 16...  2017-09-24   

                          surface_id_h3 nom_court  ID  groupe_id  
18  L2A_T58KDC_20170924_8c9e2db4112dbff     58KDC  19        0.0  
26  L2A_T58KDC_20170924_8c9e2db418f41ff     58KDC  27        0.0  
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les nom

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents


c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

...

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont différents
les noms des tuiles sont identiques.                                   nom      province     commune   surface  \
31933  SENTINEL2x_20170921_L2A_T58KEA  Province Sud  BOULO

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

les noms des tuiles sont identiques.                                   nom       province commune   surface  \
32054  SENTINEL2x_20170921_L2A_T58KEB  Province Nord  CANALA  1.940602   
32060  SENTINEL2x_20170921_L2A_T58KEB  Province Nord  CANALA  4.301334   

                                                geometry       date_  \
32054  POLYGON ((166.027 -21.530, 166.027 -21.530, 16...  2017-09-21   
32060  POLYGON ((166.027 -21.532, 166.027 -21.532, 16...  2017-09-21   

                             surface_id_h3 nom_court     ID  groupe_id  
32054  L2A_T58KEB_20170921_8c9f5159c6669ff     58KEB  32055     5083.0  
32060  L2A_T58KEB_20170921_8c9f5159c769dff     58KEB  32061     5083.0  
les noms des tuiles sont identiques.                                   nom       province commune    surface  \
32057  SENTINEL2x_20170921_L2A_T58KEB  Province Nord  CANALA   1.460471   
32090  SENTINEL2x_20170921_L2A_T58KEB  Province Nord  CANALA  31.570218   

                                         

c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\oriane.bruyere\AppData\Local\miniconda3\envs\gis311\Lib\site-packages\geopandas\geodataframe.py:1525: SettingWithCopyWarning:

In [28]:
surfdetect_control=surfdetect_control.reset_index(drop=True)
surfdetect_control['ID'] = range(1, len(surfdetect_control)+1,1)

In [29]:
# Check if the geometry is a Polygon 
for i in range(len(surfdetect_control)):
    if surfdetect_control['geometry'].geom_type[i] == 'Polygon':
        surfdetect_control.at[i, 'geometry'] = MultiPolygon([surfdetect_control['geometry'][i]])
        #print(surfdetect_control)
    else:
        print("La géométrie n'est pas de type Polygon.")

La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.
La géométrie n'est pas de type Polygon.


In [30]:
surfdetect_control['surface'] = surfdetect_control['geometry'].area/10000

## FINALISATION : Intégration des données dans la table "sentinel_surfaces_detectees"

In [ ]:
gdf = gpd.GeoDataFrame(surfdetect_control.copy(), crs=surfdetect_control.crs, geometry=surfdetect_control['geometry'])
gdf=gdf[["nom", "province", "commune", "surface", "geometry","date_","surface_id_h3"]]

In [ ]:
from sqlalchemy import text
table = "sentinel_surfaces_detectees"

conex = create_engine(f'postgresql://{os.getenv("DB_USER")}:{os.getenv("DB_PWD")}@{os.getenv("DB_HOST")}:{os.getenv("DB_PORT")}/{os.getenv("DB_WORKSPACE")}')
gdf.to_postgis(table, conex,schema=os.getenv("DB_SCHEMA"),if_exists='append')